In [1]:
import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '../..')))

# Path Configuration
from tools.preprocess import *

# Processing context
trait = "Bone_Density"
cohort = "GSE198934"

# Input paths
in_trait_dir = "../../input/GEO/Bone_Density"
in_cohort_dir = "../../input/GEO/Bone_Density/GSE198934"

# Output paths
out_data_file = "../../output/preprocess/Bone_Density/GSE198934.csv"
out_gene_data_file = "../../output/preprocess/Bone_Density/gene_data/GSE198934.csv"
out_clinical_data_file = "../../output/preprocess/Bone_Density/clinical_data/GSE198934.csv"
json_path = "../../output/preprocess/Bone_Density/cohort_info.json"


### Step 1: Initial Data Loading

In [2]:
from tools.preprocess import *
# 1. Identify the paths to the SOFT file and the matrix file
soft_file, matrix_file = geo_get_relevant_filepaths(in_cohort_dir)

# 2. Read the matrix file to obtain background information and sample characteristics data
background_prefixes = ['!Series_title', '!Series_summary', '!Series_overall_design']
clinical_prefixes = ['!Sample_geo_accession', '!Sample_characteristics_ch1']
background_info, clinical_data = get_background_and_clinical_data(matrix_file, background_prefixes, clinical_prefixes)

# 3. Obtain the sample characteristics dictionary from the clinical dataframe
sample_characteristics_dict = get_unique_values_by_row(clinical_data)

# 4. Explicitly print out all the background information and the sample characteristics dictionary
print("Background Information:")
print(background_info)
print("Sample Characteristics Dictionary:")
print(sample_characteristics_dict)


Background Information:
!Series_title	"In silico discovery of the blood cell interactome [Affymetrix]"
!Series_summary	"The aim of the present study identify putative macromolecular interactions in human peripheral blood based on significant correlations at the transcriptional level."
!Series_summary	"We found that significant transcript correlations within the giant matrix reflect experimentally documented interactions involving select ubiquitous blood relevant transcription factors (CREB1, GATA1, and the glucocorticoid receptor (GR, NR3C1))."
!Series_overall_design	"We performed transcriptional profiling of peripheral blood from Norwegian women (50–86 years, n=105) representing a cohort with varying bone mineral densities (BMDs) and free of primary diseases and medication known to affect the skeleton."
Sample Characteristics Dictionary:
{0: ['age (years): 62.5', 'age (years): 81', 'age (years): 59.6', 'age (years): 57.1', 'age (years): 81.4', 'age (years): 66.2', 'age (years): 57.7',

### Step 2: Dataset Analysis and Clinical Feature Extraction

In [3]:
import pandas as pd
import os
import json
from typing import Callable, Dict, Any, Optional

# 1. Gene Expression Data Availability
# Based on background info, this is transcriptional profiling of peripheral blood,
# which indicates gene expression data is available
is_gene_available = True

# 2. Variable Availability and Data Type Conversion
# 2.1 Data Availability

# From the series_overall_design, we know this is about bone mineral densities (BMDs)
# but we don't see it in the sample characteristics dictionary
# However, we know it's the primary focus of the study from the overall design
trait_row = None  # We don't see BMD in the sample characteristics

# Age data is available in row 0
age_row = 0

# Gender is not explicitly mentioned, but from the background information
# the study is on Norwegian women only, so all subjects are female
# This means gender is constant and not useful for our association study
gender_row = None

# 2.2 Data Type Conversion
def convert_trait(value):
    # This function won't be used since trait_row is None
    return None

def convert_age(value):
    # Extract age value after the colon and convert to float
    try:
        if ":" in value:
            age_str = value.split(":", 1)[1].strip()
            return float(age_str)
        else:
            return None
    except:
        return None

def convert_gender(value):
    # This function won't be used since gender_row is None
    return None

# 3. Save Metadata
# Determine trait data availability
is_trait_available = trait_row is not None

# Initial filtering on usability
validate_and_save_cohort_info(
    is_final=False,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available
)

# 4. Clinical Feature Extraction
# Skip this step as trait_row is None (trait data is not available in the sample characteristics)


A new JSON file was created at: ../../output/preprocess/Bone_Density/cohort_info.json


False

### Step 3: Gene Data Extraction

In [4]:
# 1. Use the get_genetic_data function from the library to get the gene_data from the matrix_file previously defined.
gene_data = get_genetic_data(matrix_file)

# 2. Print the first 20 row IDs (gene or probe identifiers) for future observation.
print(gene_data.index[:20])


Index(['7892501', '7892502', '7892503', '7892504', '7892505', '7892506',
       '7892507', '7892508', '7892509', '7892510', '7892511', '7892512',
       '7892513', '7892514', '7892515', '7892516', '7892517', '7892518',
       '7892519', '7892520'],
      dtype='object', name='ID')


### Step 4: Gene Identifier Review

In [5]:
# These identifiers appear to be probe IDs (likely from an Illumina microarray platform), not gene symbols.
# They are numerical IDs, which is typical for microarray probes, and need to be mapped to human gene symbols.

requires_gene_mapping = True


### Step 5: Gene Annotation

In [6]:
# 1. Use the 'get_gene_annotation' function from the library to get gene annotation data from the SOFT file.
gene_annotation = get_gene_annotation(soft_file)

# 2. Use the 'preview_df' function from the library to preview the data and print out the results.
print("Gene annotation preview:")
print(preview_df(gene_annotation))


Gene annotation preview:
{'ID': ['7896736', '7896738', '7896740', '7896742', '7896744'], 'GB_LIST': [nan, nan, 'NM_001004195,NM_001005240,NM_001005484,BC136848,BC136867,BC136907,BC136908', 'NR_024437,XM_006711854,XM_006726377,XR_430662,AK298283,AL137655,BC032332,BC118988,BC122537,BC131690,NM_207366,AK301928,BC071667', 'NM_001005221,NM_001005224,NM_001005277,NM_001005504,BC137547,BC137568'], 'SPOT_ID': ['chr1:53049-54936', 'chr1:63015-63887', 'chr1:69091-70008', 'chr1:334129-334296', 'chr1:367659-368597'], 'seqname': ['chr1', 'chr1', 'chr1', 'chr1', 'chr1'], 'RANGE_GB': ['NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10', 'NC_000001.10'], 'RANGE_STRAND': ['+', '+', '+', '+', '+'], 'RANGE_START': ['53049', '63015', '69091', '334129', '367659'], 'RANGE_STOP': ['54936', '63887', '70008', '334296', '368597'], 'total_probes': [7.0, 31.0, 24.0, 6.0, 36.0], 'gene_assignment': ['---', 'ENST00000328113 // OR4G2P // olfactory receptor, family 4, subfamily G, member 2 pseudogene // ---

### Step 6: Gene Identifier Mapping

In [7]:
# 1. Identify the correct columns in the gene annotation data for probe IDs and gene symbols
# The 'ID' column contains the probe identifiers that match the gene expression data index
# The 'gene_assignment' column appears to contain gene symbol information

# 2. Extract these columns to create a mapping dataframe
gene_mapping = get_gene_mapping(gene_annotation, 'ID', 'gene_assignment')

# 3. Apply the gene mapping to convert probe-level measurements to gene expression data
gene_data = apply_gene_mapping(gene_data, gene_mapping)

# Normalize gene symbols to standardize across the dataset
gene_data = normalize_gene_symbols_in_index(gene_data)

# Print a few rows to inspect the result
print("Gene expression data after mapping (first 5 genes and 3 samples):")
print(gene_data.iloc[:5, :3])


Gene expression data after mapping (first 5 genes and 3 samples):
         GSM5961154  GSM5961155  GSM5961156
Gene                                       
A1BG       0.859520    0.888765    0.857480
A1CF       0.248888    0.276548    0.256452
A2M        0.559986    0.571946    0.545696
A2ML1      0.554328    0.561175    0.539393
A3GALT2    3.843910    3.945310    3.765470


### Step 7: Data Normalization and Linking

In [8]:
# 1. Normalize the obtained gene data with the 'normalize_gene_symbols_in_index' function from the library.
# This was already done in Step 6, but we'll ensure the data is saved
os.makedirs(os.path.dirname(out_gene_data_file), exist_ok=True)
gene_data.to_csv(out_gene_data_file)
print(f"Normalized gene data saved to {out_gene_data_file}")

# We need to validate if we have trait information before proceeding
is_gene_available = True
is_trait_available = False  # As determined in Step 2, trait_row was None

# Create a minimal DataFrame to satisfy the function requirements
minimal_df = pd.DataFrame({trait: [0]})  # Just a placeholder

# Record the cohort information - this dataset has gene data but no trait data
note = "Dataset contains gene expression data but no bone density measurements in the sample characteristics."
is_usable = validate_and_save_cohort_info(
    is_final=True,
    cohort=cohort,
    info_path=json_path,
    is_gene_available=is_gene_available,
    is_trait_available=is_trait_available,
    is_biased=False,  # Not applicable but function requires a value
    df=minimal_df,  # Minimal DataFrame to satisfy function requirements
    note=note
)

print("This dataset is not usable for trait association study as it lacks trait information.")

Normalized gene data saved to ../../output/preprocess/Bone_Density/gene_data/GSE198934.csv
Abnormality detected in the cohort: GSE198934. Preprocessing failed.
This dataset is not usable for trait association study as it lacks trait information.
